## Learning objectives


1. Running python scripts

2. Writing functions

3. Understanding assert statements

4. Parsing FASTA files

5. Writing a k-mer counter

---

## Running a python script from the command line

There are several ways to run a python script from the command line. We have been using one, passing a script to the python program. Alternatively, we can make the script executable itself.

```bash
>chmod a+rx SCRIPT.py
```

This means that we can now call our script, either using a direct path to it

```bash
>./SCRIPT.py
```

Alternatively, the script could be put into any folder listed in the `PATH` environmental variable.

However, running any of the scripts we've seen so far give us an error. Why? The computer doesn't know what language the code is written in so it defaults to the language of the shell you're in (we're in bash). So how do we fix this?

### The Shebang!!!

The shebang is a special comment at the beginning of the script that tells the computer what environment to run the script in. We can even use it to tell the computer a specific version of python to use.

In [ ]:
#!/usr/bin/env python3

Now we can run our script as a stand-alone program and the computer will know how to run it as a python script! The same thing works for any other non-compiled language scripting.

## Writing functions

Anytime that you may want to run the same set of operations more than once, a function is a convenient way to save writing the code over. Functions also allow you to create much more readable and understandable code. Function definitions contain four parts, the word "def" to let the interpreter know that you're defining a function, the name of the function, the arguments that the function can take, and the code to execute.

In [ ]:
def my_function(arg1, arg2):
    arg1 += arg2
    return arg1

Arguments to a function have a specific order and the order that you pass thenm to the function will correspond to the order they are given in the function definition. However, you can use the names of the arguments in the function definition to pass arguments in different orders.

In [ ]:
a = my_function(arg2=5, arg1=1)
print(a)

Sometimes you don't need to define every argument everytime you call the function. You can define default values when you define the function. However, you need to put all variables without default values before those with defaults.

In [3]:
def my_function2(arg1, arg2=0):
    arg1 += arg2
    return arg1

There are two ways that functions can pass back information. The `return` statement will end the function and pass back whatever follows the return. If there is no return statement, then the function returns `None`. The second way is to pass a mutable variable to the function. When a function is called, immutable variables remain unchanged by operations in the function. Mutable variable types, however, allow changes within the function to be maintained after the function call finishes.

In [4]:
def my_function3(arg1=0, arg2=[]):
    arg1 += 1
    arg2.append('a')
    
a = 5
b = [5]
my_function3(a, b)
print(a)
print(b)

5
[5, 'a']


What can we do if we have many different results that we want to return from a function? Given the following function, can you edit the code to return all of the variables that we created within the function?

In [ ]:
def multiple_results(n):
    squared = n ** 2
    cubed = n ** 3
    text = str(n)

Functions can also be called recursively. That is, a function can call itself. This is very useful for things like traversing a tree. Let's try finding a factorial value.

In [5]:
def factorial(n):
    if n > 1:
        return n * factorial(n - 1)
    else:
        return 1
    
print(factorial(5))

120


If you haven't encountered it by now, one of the quirks about (but not limited to) python is that it is interpreted linearly from top to bottom, which pratically means that you can't refer to anything that hasn't been defined above it, including functions. So, if you have functions but the main part of your code is outside a function, you have tp pay attention to ordering. As you can see, the following doesn't work.

In [6]:
a = some_function()

def some_function():
    return "my value"

SyntaxError: unexpected EOF while parsing (<ipython-input-6-63f860db0740>, line 3)

Therefor it is useful to enclose ALL of your code in functions. Traditionally, the main part of your code will occur in the cleverly named `main` function. 

In [8]:
def main():
    a = some_function()
    print(a)
    
def some_function():
    return "my_value"

# main()

# if __name__ == "__main__"

SyntaxError: invalid syntax (<ipython-input-8-1d5dbfde6e47>, line 2)

But, that code doesn't seem to do anything!!! Why not? Can we fix it?

## Defensive programming

One thing to watch out for is code being executed in a way that you didn't intend. Therefore its important to check that things are what you expect before moving on. 

In [0]:
def test(a):
    assert a > 5, 'Value is too small'
    print('Value is big enough')

test(10)
test(2)

## Parsing a FASTA sequence

Now, let's use our new found skills to read in a FASTA file. The FASTA format is used to hold raw sequence. Each sequence begins with a ">" followed by the name of the sequence. All of the lines following this until then next name line or the end of the file are the sequence associated with that name, broken by line breaks for readability. So, let's break down the steps we'll need to take to read in a FASTA file with a single sequence. And let's do it in a function that accepts a file stream as an argument.

### FASTA format


<br><div style="background: #EEE"> \>sequence 1<br> AGATCTCCCTGAGAGAAGAGCTCTCTCTCGA<br> TCTCGGATTACGTAGGCTAGAGAGAGAGCTA<br> TTCAA<br> \>sequence 2<br> GATCTCGGGATAAAAAAACTGGGATCTGATC<br> ATCTAAAGAGAG </div><br>


1. read in the name line
2. strip off the newline and ">" characters
3. create something to hold the sequence
4. read a line of sequence
5. strip off the newline character
6. put the sequence in our sequence variable
7. repeat 4-6 until we reach the end of the file
8. return the name and sequence

In [9]:
# Let's have it accept an open file object
# That way it can be passed a file or standard input

def single_FASTAReader(file):
	# Get the first line, which should contain the sequence name
	line = file.readline()

	# Let's make sure the file looks like a FASTA file
	assert line.startswith('>'), "Not a FASTA file"
	
	# Get the sequence name
	seq_id = line[1:].rstrip('\r\n')

	# create a list to contain the 
	sequence = []

	# Get the next line
	line = file.readline()

	# Keep reading lines until we run out
	while line:
		# Check if we've reached a new sequence (in a multi-sequence file)
		if line.startswith('>'):
			break

		# Add next chunk of sequence
		sequence.append(line.strip())
		
		# Get the next line
		line = file.readline()
	return (seq_id, ''.join(sequence))

To test this, we'll need a FASTA file so copy `/Users/cmdb/qbb2021/data/subset.fa` into the same directory as this notebook.

In [13]:
name, seq = single_FASTAReader(open('subset.fa'))
print(name, seq)

STRG.1.1 CACACTAGACCCACCGATCGCGACTTTGTGTGTGTTAAAATGACGCGCATATCGTTTTGGGCTAATAATATTGTTCACGTTTTATAAAACAGATACACGGTTAAGCTCTGACCGGTCGTATTATTATCTGTGTGTTCTTGGTTGACACGTTTATTTCATTTATTCTCATTTAAAGCAACGATGTGAAGAACAGTGCGGGCGTTTCTCAACATAAGAATACATACAAACTTATGCGTGTTGGTGAGCAAATAAAATAGTTCAAAAAATTACTCGGCCACCGCCTTAACCGTACAAACGGAAATACATAAAGtttaGAATAAATACGGCCACAATTAGTATACATATTTATTCATCGAAACCAACCCACCACAAGAGCATAACCAATTATGTTAAAGTTTATCAGAGGAAAAGGGCAGCAGCCCAGTGCTGACAGACACCGCCTACAGAAGGACCTTTTTGCTTATCGTAAGACGGCACAGCATGGCTTTCCTCATAAGCCTTCGGCTCTTGCGTATGATCCAGTTTTGAAACTTATGGCAATAGGGACGCAAACAGGGGCTTTAAAAGTTTTCGGTCAACCCGGAGTTGAATTGTACGGTCAGCATACTTTGTTAAACAATTCAGCATCGGAGCTTAATGTACAATTACTTGAATGGGTGTATGGAACTGGTCGCATACTTTCGTTGACGGCAGCGAATCAATTAATTCTATGGGAGCCAGTTGGAGCAACGTTGCTGCCAATCAAAACACTACCGTTTGACGGCAAACTTAAAAAAGTTTCATCGCTGTGCTGTTCTCTCAGTAAGGATCTGCTATGGATTGGAACAGAAGGTGGAAACATCTATCAACTGGATTTACATACATTTACCATTAAGGAGCCTGTAATTTACCATGACGTTGTGCTAGAGCAGGTGCCACCAGCCTACAAGCTAAATCCTGGTGCAATTGAGTCAATCCGCCAACTTCCAAACTCCCCTAGCAAACTTCTAGT

## Parsing a FASTA file

Now that we've read in a single sequence, let's alter that function to read in all of the sequences in a file. How do we need to alter the function?


1. create a container for all of the sequences
2. read in the name line
3. strip off the newline and ">" characters
4. create something to hold the sequence
5. read a line of sequence
6. strip off the newline character
7. put the sequence in our sequence variable
8. repeat 3-7 until we reach the end of the file
9. put the sequence in our sequences variable
10. repeat 2-9 until end of file
11. return sequences

In [18]:
def FASTAReader(file):
    # Get the first line, which should contain the sequence name
    line = file.readline()

    # Let's make sure the file looks like a FASTA file
    assert line.startswith('>'), "Not a FASTA file"
    
    # Get the sequence name
    seq_id = line[1:].rstrip('\r\n')

    # create a list to contain the 
    sequence = []

    # Get the next line
    line = file.readline()

    # Add a list to hold all of the sequences in
    sequences = []

    # Keep reading lines until we run out
    while line:
        # Check if we've reached a new sequence (in a multi-sequence file)
        if line.startswith('>'):
            # Add previous sequence to list
            sequences.append((seq_id, ''.join(sequence)))
            
            # Record new sequence name and reset sequence
            seq_id = line[1:].rstrip('\r\n')
            sequence = []
        else:
            # Add next chunk of sequence
            sequence.append(line.strip())
        
        # Get the next line
        line = file.readline()
    # Add the last sequence to sequences
    sequences.append((seq_id, ''.join(sequence)))

    return sequences

In [19]:
seqs = FASTAReader(open('subset.fa'))
print(len(seqs))
print(seqs[0])
print(seqs[1])

105
('STRG.1.1', 'CACACTAGACCCACCGATCGCGACTTTGTGTGTGTTAAAATGACGCGCATATCGTTTTGGGCTAATAATATTGTTCACGTTTTATAAAACAGATACACGGTTAAGCTCTGACCGGTCGTATTATTATCTGTGTGTTCTTGGTTGACACGTTTATTTCATTTATTCTCATTTAAAGCAACGATGTGAAGAACAGTGCGGGCGTTTCTCAACATAAGAATACATACAAACTTATGCGTGTTGGTGAGCAAATAAAATAGTTCAAAAAATTACTCGGCCACCGCCTTAACCGTACAAACGGAAATACATAAAGtttaGAATAAATACGGCCACAATTAGTATACATATTTATTCATCGAAACCAACCCACCACAAGAGCATAACCAATTATGTTAAAGTTTATCAGAGGAAAAGGGCAGCAGCCCAGTGCTGACAGACACCGCCTACAGAAGGACCTTTTTGCTTATCGTAAGACGGCACAGCATGGCTTTCCTCATAAGCCTTCGGCTCTTGCGTATGATCCAGTTTTGAAACTTATGGCAATAGGGACGCAAACAGGGGCTTTAAAAGTTTTCGGTCAACCCGGAGTTGAATTGTACGGTCAGCATACTTTGTTAAACAATTCAGCATCGGAGCTTAATGTACAATTACTTGAATGGGTGTATGGAACTGGTCGCATACTTTCGTTGACGGCAGCGAATCAATTAATTCTATGGGAGCCAGTTGGAGCAACGTTGCTGCCAATCAAAACACTACCGTTTGACGGCAAACTTAAAAAAGTTTCATCGCTGTGCTGTTCTCTCAGTAAGGATCTGCTATGGATTGGAACAGAAGGTGGAAACATCTATCAACTGGATTTACATACATTTACCATTAAGGAGCCTGTAATTTACCATGACGTTGTGCTAGAGCAGGTGCCACCAGCCTACAAGCTAAATCCTGGTGCAATTGAGTCAATCCGCCAACTTCCAAACTCCCCTAGCAA

## K-mer counting

A k-mer is an arbitrary length sequence. One characteristic of genomes is that some k-mers are reused often while others are rare or absent. This can allow us to distinguish different species by k-mer distributions, identify copy numnber variation, repeat expansions or contractions, etc. It is also used in sequene alignment. Now that we've got a function for reading in sequences, let's break those sequences down into k-mers and count the occurance of each k-mer. But, what steps do we need to do this?

1. read in fasta file.
2. specify the length of the k-mer to count
3. create a variable to record k-mer counts (what kind?)
4. set position at base zero
5. get k-mer from position to position + k
6. Add k-mer to results or add a tally to results
7. advance position by 1
8. repeat 5-7 until k-mer would run off sequence
9. repeat 4-8 for each sequence
10. return results

In [20]:
reader = FASTAReader(open('subset.fa'))
kmers = {}

k = 11

for seq_id, sequence in reader:
    for i in range(0, len(sequence) - k):
        kmer = sequence[i:i + k]
        kmers.setdefault(kmer, 0)
        kmers[kmer] += 1

for key in kmers:
    print(key, kmers[key])

GTACAAGAATG 1
AACACCCTTCT 1
AGTATATAAGA 1
CCACCTGTAGA 1
CGTCTCCGCAA 2
CACCATGGCTC 3
TTCGCTTATAA 1
CGATTGAAACA 2
TGGGACATAGC 2
AACTGCAACCA 2
TATTCATTTTT 1
TTTGGCAGCGG 1
AATAGTTCAAA 1
CTTTGGAAGGG 2
CAGAGCCCACA 1
TGAGTTCGAGG 2
CTGTGTGCGGT 1
GTATAAACACA 1
TGGACGTGGTG 1
GATGTGGACAG 2
ATTTTGCTGAC 2
GCTCAGCTGCT 1
TGGTCATAAGC 1
AATAGCTATTG 1
CTGAGCTTTAT 1
GGACTACGCCT 2
ACAGTCTGGAA 1
GCTGAGGGCAT 1
GCCCTTGCATT 1
ATGATTCCCGA 2
TTGAGCTACTG 2
GGGCGCATCAC 2
TCAGAATGCCA 2
AAAACTTAAGC 1
GCTCGTTCCAC 2
CATACCACTGT 2
CCTGGATGCGA 1
AGGATAAGCAG 1
TTTTCCTAATA 1
GCTATTATCAT 2
GCCAGAAGAAA 2
GGTCATCAGGG 2
TGCAGCCAGGA 2
ATTGATCTTTC 1
GTTAAGTCTGG 3
CGTGTGTATAT 2
TAAGTATTCAA 1
TCGAGGAGCAC 1
GAGGGCCTCCT 2
TGGAAAAGAAG 2
TGaaattattt 1
GGAATTGCAAA 2
CGCACGTTCCT 1
AGGGCAAGCAC 1
AGCTTCAGACA 1
CACTCAAACCG 1
TTGTGAGCGGA 1
GATGTGCCTGC 1
CAACTTTGTGG 1
GCCACGTCAGC 1
TCAGAAAACAG 2
TCACAACCACT 2
TCCCGATTCCT 1
ACACAACTTGG 2
TGAATCGTATT 1
CTAATGAGACA 1
GGATTTTATGT 1
ACGACTACTAT 1
ATGAGGATGAG 2
TTATTTTGTTC 1
TCTTACCTGTA 1
ATGGAT

ATCTACATTAA 1
CACCAGGAAGA 2
CATTAAGTTTC 2
AGCTCAACCAC 2
TTGATTACCAG 1
ACGCTAGCGCA 2
TAGTCTACTTA 3
AAATACTATTT 2
GAACATCTCGG 2
AGCGAGAACCG 2
ATGGTGATGAT 2
TGCTGACCATC 2
AAGATCTTCCC 2
TCTTATCTAAG 2
AATATTAAATA 2
TTCCTTTAGCC 2
ACCTGCCCGGT 2
CCGAAATCCAG 2
AGCGGGAGCTG 3
TTTCTGAAAGA 1
GCCCATGACTG 3
CCTTCAATTGA 1
CTTTGTGCCCT 1
TGTGAGTCTAT 1
GACATCAGTCG 2
AACCGGTATCA 2
AAGCATCAATG 3
ACCGGCGGGCT 2
TTAAAACCGTC 1
ATCCTCAAAAC 2
GCCGCGTAGCT 2
CAggaggaagc 3
GACCTGGCTGT 2
AGGTGCATCGT 1
AACAACCCAGC 2
TTGCTGCCAAT 1
GTGGTGGTGCC 3
CCGCAAGAAGG 2
GCGTTAAACGC 2
ACAGGAATATA 1
GCATCAAAAGC 1
CGCGGCCGAGC 2
TGGCCCTGGAC 3
TGTTACCGCCA 2
CGGCTGGTTGC 1
ACCCCGCCTAA 2
AAATTTTCAGA 3
TCCACCTGTAG 1
CTTAAAGGATC 1
CTTACCCCTTA 3
cacctcctaag 1
CGAAAACAATT 2
TGCCGGAGTCC 2
CGCCAAGGCAC 2
GATTTTTGGGG 1
TATGAAAACAT 3
TTGGTAATAGT 1
GCAAATAATTA 3
gcagctacaac 2
GAGGGTAATAA 2
AAAGAGCGACA 3
GAGATCGCTGC 4
TTCTTCATCAT 2
ATTCGACGATA 2
ACAAACTCCAC 2
TCCAGCCGGGA 3
TTGTGAACAAT 1
GTCTTGGATCC 2
AGTGCCttttt 2
GCGTGCTGATG 3
CTAAGACAGTG 1
TAACAG

AGAAGACCTTT 1
AATAAAATACT 3
GGCACACTCCT 1
AGCATATCGGT 2
CCTATCAAAGG 2
CCTGCAGTTCC 3
AGATCAGACCA 2
CGCTATTTAAC 4
TTGAGCCAACG 1
AGGTCGACAGT 1
TCTAAATCTAA 1
CTGGGCCTTTG 1
CGTGAAAGATA 1
GCCCACATTTT 1
TAACCAAAGCA 4
CGCAGATGCaa 2
ACTAAAAGTAT 1
TCAATTTGCTG 1
ACCTCAAGTCC 1
GAACTACGAAT 1
ACGTAAACTCA 1
CTGCTTTGAGC 1
AGCAGCCACAG 2
GGAGTATGTGG 2
ATGTAACAGAA 2
ATCGTGGGAGC 2
ACCAAGCCGGT 3
atacatatacG 1
TCACAGGTATG 1
GGGAGGGAACT 3
CGTAGGTGCGC 1
CTGGAAATCAA 2
AGGCCAAAGCA 3
GAATGAGGCCT 1
ATACTTCAGCT 3
TGAATGAAACT 1
ATAGAAAGCAA 1
CGATGAGTTGT 2
ATGCCAAGCCT 1
CCAAAAAAGAA 4
GAGTCCTTCTC 1
TTGGACGAATC 3
ACACCGCCGCC 2
CAGAAGCAGTG 2
CTTAGCGGTGA 1
TATGACTACGA 3
AGCTCGACTTC 2
CGTGCGCTTAG 3
AGCGCTCGTTC 2
CCTGCAGTTCG 2
CCGGCAAGGTA 2
GACGCAGCCGT 2
CGAGCGGATCC 2
TCAATAAAACG 2
CAACCGACCAt 1
GCCTTGATCAT 1
AGACGCGCCGC 2
TAACACGAGTC 3
CATTAAAGCCA 2
AAACCGTTGCA 2
CGACTAAACCG 2
ATAGATAAACT 1
TCAGCTTCCAT 3
CCAGTTTGGTG 2
GGCAGGGCGCT 2
ACTTCTGGCTC 1
AGCCTTGGCCA 2
TACGCATGGCC 2
TTGGAAGCGTT 1
TTACGCCAGAA 1
ATCGCAGTTCT 3
TCTTCA

AGACCATTCAG 1
GTGGATGTCAA 3
CAGCTGCTGGG 2
ACCCTAACCAG 3
GACAGCGGCCC 2
AGCATAGTGGC 1
TAGTAGTCTCA 2
CCACCAAAGAG 2
GGGGCGTGACC 2
CCGTGCGTCAT 1
CAAGGAAGTGC 2
GAAATGTTGCT 1
AAGCGAACAAC 2
TCTGCGATTCG 2
GGGCTTTCTTC 6
TTAAGTCTGGG 3
GCCGAACCTAA 2
TTACTATATGC 2
GCACGATTCCA 2
ACTTTCTGGTT 1
ATCGCCCTGCA 2
ATTCTCTACGT 2
AGTGACCACGG 1
AGGGATGGACA 3
AAAGTAAAATC 1
GGCACATACGA 3
attttgccttt 2
CTATGGTGTCT 1
TCAGTTCCGGA 3
AGTGACACTTA 1
CAAATGCCTAC 2
ctgaaccagaa 2
TTTGCTTGTGC 3
GAGAGTACAAA 3
TCGACTGCAAC 1
TGGACACCATT 2
CGATGACAGTC 3
GAGTGCTTTTC 2
ACAATCGCAGC 2
CAAACGTTCAG 1
GGTGGCTCTGC 3
CAGGAAACCCC 2
CGCCCTGCCCG 1
CTGCTTCAGAA 2
TTCGAGGACCT 1
GTGGACTCGCA 1
GGCCAAAAGTG 1
GATGGTTCCTT 1
CCCTCGGTTTT 1
GCGGACAACCA 1
CGCAACCTGAT 1
TGAAGTTGCTA 1
GAATAAATGGA 2
AGGGCGGAAAT 2
GAGTTTTAGAG 1
CATTGCCCTGG 1
GCAGGAGgaaa 2
TTCTGCGGAAG 2
TAACACATCCa 2
TATACTGTCTG 1
GCAAGCGAGGT 1
TTATGATATAC 1
GCACAGACACA 3
CTTCCGCGGCG 3
TCTCCTCGTCT 1
CATCTTCCTCA 2
ggatacagata 1
AGCTGGGCGTT 3
ATTCGCCAAGG 1
AGAGCGTTCGG 3
AGGGTTACTCA 1
AAACTT

TGAACGGGTGA 1
ATTTCGGAATT 1
AACATCGGATC 2
ATTTTTGGTCG 1
GTTGGGGCTGA 2
CAGGACTACTT 1
AGTGGGGGGCT 2
AGTGCAACACG 1
AAACTCACTCG 1
TCAGTGGCAAT 1
CCAAACGTCAT 1
AATGCGAAAGA 4
TCCTGGAGTGG 2
GCCATCCTGAT 2
ACATGATGTAC 2
GCAGTCATCTG 2
CCCCCAACCAG 1
TTACCGATGAG 1
AACAATTCGCT 3
AGCACATCCAT 2
GCAGTCGGAGG 2
CCTTTACCACA 3
CCCGTTCCGAT 2
CTGGAAACGCC 3
tcgagcagctc 3
GTTGAACGACT 2
GCGCCTAAACG 1
TTGGTAAACAA 3
GTTAAAAATAA 2
CTGGAAGTCCG 3
ACAATCCGAGC 2
GGGAGTGCGCC 7
gtttggtttcg 2
GAACGTGAAGA 2
CTTCAACCTGG 1
AATGCCTCGGC 2
ACTTACCcaca 1
cggtagcggca 2
CTCGAGGACAC 3
GTGAAGGGAAA 1
GTCACTCTCTT 2
ATTGTACCTGA 2
TTGCCTGCGGA 1
ATAATTAGACA 1
AATGCCCGCGC 3
CTCGGTTTTCC 1
TCATAGCCGCT 1
GCGTGAAAAGC 1
ACTGAGCACGC 2
AGCAGTAGAGA 2
AACAGCCAGCT 1
CATGtttttat 3
AGAAGGTCATG 1
AATCATCAGCC 1
ATGGCTTTCAG 1
CGCGGAGAGCA 2
CTGCACAACCT 1
caccatcaaca 2
CAGGTCCGGAT 1
AGCAACTACGT 1
ACCTCCATTGC 2
ACGCATTTTAA 1
AGGGAGCGCCT 1
CAAAGCAGGAT 2
GAAATGAGAAG 1
ATTTATCCGAT 1
CCCGAGCTCGC 3
GCATGGCCCCA 2
CATTCAACAGC 1
GGGAGGGCGGG 3
AGGGCAGTGCC 2
TATTGT

...

CACCTGTCagt 2
GACGGGGAGCA 2
GACCTGGTGGG 2
CAGGCACCTGC 1
TTTCCTCTGGA 2
TCGCTGACGAA 2
TGCCCACTGTG 2
AATACCCTGTG 2
CTCTATTGTAG 2
TCTGATGAAGG 2
GAGGAACTTAC 1
CGAGCGGCCAA 2
gctaaacagga 1
GTATCCGGAAT 1
ATAGCGATGAT 1
CAAGCTAGTGT 1
TTCCTTTATAC 1
AGTAGCTACAG 2
TGTCATTTCCT 1
AAAGTTCTGGT 2
CCTGCCCATGA 3
GTGTGCTGCAA 1
ACGTGGAGACC 1
GAATAATATTG 1
TGCTTACCATT 1
TTCCTGCGCAG 2
AAGTTGAACCC 1
CAGCATGTGCC 2
ACGCaaaaaaa 1
GGAAAGCCCGG 1
GAAACCACAGG 1
TTCTGTTCGTC 1
TGCCCAATCCT 1
GAGCGCCTGTC 1
CGGCCATCAAC 1
GAGAACATCGA 1
CTACATGGAGA 2
GTTCTGGTGGC 2
TGTGCTGAGAC 1
ATTAAACTCTC 1
GCAGCGCGAAC 2
CTCAGATTCAA 3
GCCAGCCGAGA 2
GCAGCGGCACT 2
TAAGACTAAGT 1
CGGCTATCCGC 4
GCGTTCGTACA 1
ATGCGTGGCAA 2
AATATTAAAAT 1
GTTGGAGTCGC 2
TGTCTCTTTTA 6
ATCTGAACTCT 1
ACATCTGGCAA 2
TTTCTGTGTGC 2
ACCAGACCCCG 2
CGAGCAGAGCA 3
CCAACACGTAA 1
CTGCTGGATGC 2
CCTGAGACTGC 1
agtcagcGCCG 2
GGGAGCGCAGC 3
GTTGAAAACGT 1
TAAGCCAGAGC 2
GCTTCTGCTCA 2
TGTGAAGAGCG 1
TCATTGTCTGA 1
GTGGAGGATGC 1
CTGAAAAACCA 1
GGCAAAATACG 1
gccctgcagca 2
GCTGTAATCCT 2
TTGTTG

GGATGGCTCCT 1
CGCAGCATCAA 1
TTGCTCGGCGT 2
AGAAACCCAAT 5
TAAGGAACCCG 3
GAGGTCTTGGC 2
GATGCTATGAT 1
TCCGTGTTTAA 3
AATCAGCACCA 2
GGCAACCTAAG 1
ATGAGCAGCTC 2
GCTATTTATGA 1
ATAGTTGTCAT 1
CAGCTTAATCC 1
TCCGATCTTTG 1
GACAGCACTGA 3
ACTAATTAAAG 3
GGCAATGGCGG 3
GCCGAACTGGC 1
TTTGGATTTGC 3
GGTTTTCCTTC 1
GGAACTGGAGT 2
AAGACACCTAA 1
CGCTCTCAGTA 2
GGTTTGTCGTC 1
AGATCGCCCGT 2
ATGTAGCACTT 1
CACTGGTCACA 2
TACCcacacac 1
AATCGTACCTC 1
GCGGCTTTGTG 1
GGTTGAAAAAA 1
CCAGAACCATC 2
AGGGCCTAGCA 1
TGCATATGCAG 6
TCCGCCTGGTT 2
CATTGATTCTT 2
TACACGACAAC 2
ACCCGGACCAA 2
GATAAGCAGTT 2
GGTCTTTATTT 1
CAGGTTGTACA 1
ACCAGGCGGCT 2
TGTTAAACGCT 1
ACTTTCAGGAG 4
ATGCGCGCCGA 2
TCAGGATCTTA 1
TACATTTTCAA 3
GCAGGGTACAT 1
TTTTAATATCG 1
TTTGTCTTCTG 3
AAACTGCAAAT 4
TGAAATTAATA 1
GATACGTGTCG 1
ATCGTAAACGT 2
AGAAAACGACC 1
GTGATACACGA 2
ttcggtaccgt 1
AGAAGATGTAG 2
GATGAGTGTCT 2
AGGTGTCACAA 3
CAGAACTTTTA 3
CCACAAACTGA 1
CGTTTGCAAGT 2
AGAGCGCGCCG 2
TTGAGTTTAGC 2
AACTTCAACAA 2
AGGATTACATA 2
GCGTGGCTCCA 2
GCTCAACTGGT 2
AAACCATGTCA 3
TGCCAA

TACAGTGCCTT 5
ACTAAGTGGGG 2
TGACCAGGAGC 2
ACACATCCGCC 1
CGACAGAAAAA 3
GTCTTAATTGG 2
GGCGGAACACC 1
GCTGATCGCGT 1
GAAGACAAAGA 1
GAATTATGGAC 3
TTTATCTGCAA 2
CGGTGACCGAC 2
AACAGTGCAAT 1
GCCCCCTGGGT 2
TAAGGCAAGCC 5
CTCAAAAGATA 2
GAAGGGCCACA 1
TAGTTCGGTTT 2
AAACACGGCTG 3
GCAGGCGAGGG 1
ACTGTCAGCAC 2
CCAAGGTTCTG 1
GTTCTACAATG 3
TACCAACAAAA 3
GTGAACCGAGA 2
GAGCTACTCCT 2
TCATCATCATG 3
CGCTTCTGAAA 1
TGCGGCAAGAA 2
TTTAAGAGCTG 1
CGACGGCGAGA 2
GGCACGGACTT 1
CGAGTACTTCT 2
CCCATAAACAT 1
CAAATCTCTAC 2
TGCCTCGGCTC 1
aacacagccga 2
CTGGTGCACTT 1
CAGAAGCAAGC 1
AGATCGCTCTT 3
TCGACAGCATT 2
AAGAAGATGAA 1
TGTGCCGGCTC 1
CGTCAGTCTTC 2
CGCAGGACGGA 2
ACGAACTGTCT 3
CAGCCGCAAAC 2
GAAGCCCACAT 3
GGAGGAACCAT 1
AAGTCGGAAGA 1
aaagagaaaaa 4
AGCGGAAAACT 2
TGGGTAAACGA 1
CACCTCGCTTT 1
GATGGAATGCT 3
CCAAGACCGGT 3
GTGGCGCTAGC 3
ATAACGCTCTA 1
GTACCTTCTGG 1
CAGACAAAAAA 3
CCGTGTGCAAC 3
ctgctgccgcc 2
AAGGACCAACC 2
GACCTTGATGA 3
TAAAGGCAAAG 2
AAGGCAATGGC 2
AAGGTTTACGA 1
CTCCAGGGTAT 3
TGTGCCACGGA 1
AATGGTAGTGT 2
TAAATTTCTTT 1
AACCTT

ATGCGACTAGA 2
GTTCGGAATCA 2
TCGTGCATTCC 2
CGCAGATTCCT 1
GCGGAGAAACC 1
CATATGTACAT 1
TGGGACAGCAG 2
GATGCTAGAGC 2
ATCATTGCATC 1
TATACTGTATC 2
GCTGAGccacc 1
CTTACCAAAAG 1
TAAATGCAAGT 1
CAACGGCTGCG 4
AAACTTCCACC 2
TTGCTCACAAA 1
TGGGACTGCGC 1
ATTTTTCGATG 3
GTGCGCTCCAT 3
GCGCCCATGGA 1
GCAAGATCGTC 3
ATCCATTCTTA 1
GAGCAAGAAAC 1
GAGCGAGTCGA 1
TGCTCCGTTTC 2
CGAAAGTGCGG 2
TGTAACTGCAG 1
CGCCATTTTCG 1
TGAAGTGGTGG 2
GGCGGGCTCTA 3
ATCCTCACCAG 2
GGAAAAGGAGC 4
CTAAACAGAGA 2
AGTCGCTCGGA 3
AACCATGTCAC 3
ACCATCGATAG 1
CCGGGTGGATA 3
AACGAGTCCAC 2
CAAGTTCAAAC 3
TTGTATCGCGA 3
CAGGCTGTGCC 2
ttaaaaaaaag 1
TGGAATGGAGT 1
CATACATATTT 1
TACGGCGTGAT 1
TTTTGAAGATT 1
GAGGCAGCCCA 2
GTTTATCTTTC 2
TGAGAATCAAG 1
GGAAAGGGGCT 3
GCAAAGTTTAT 1
agcaacatcaa 9
GTTCTTGCTAT 1
GAATGTCTCCG 1
AGGCAATCTGT 1
GCCATGCGTAC 2
ATCACACTGCT 1
ACCCAGGAAAA 1
TACGACCTGGT 1
GGCAGCAACAA 2
ACACGGTAATG 2
GAAGTTTTTAC 1
GCCACGCCTTT 2
ATTGGGCTAAG 3
TGCTAGAATCA 1
GCTGATAGCTA 1
tgtaaattaat 2
TTGCTCACCAT 1
ATCTGGATTGG 2
GTTGTGGAACG 2
ATACGCCTCAG 1
GAATAA

AGCGATCAGGA 3
GCGTCATTTAT 2
CTAATTTTACT 1
ATCTGCGGAAG 2
GTTTATGGGAC 1
AACTGGGTTTC 1
GCCTGCTGGGC 2
TCATCGAATCC 3
AGCGAGCTGGT 2
GCTAAAGGCAA 2
TGGAGTCACTG 2
CTCATCTCCAC 1
GAAGTCAGTCA 1
TGAGTTTAGCT 2
GGATAGAAACA 1
CCCAAGCCAAC 1
ACTGCCCTCCG 3
TTCAAATGGGG 2
ATCGAGAATAT 2
GAGAGCAACTA 1
ATTCCAGTGCT 1
GAGTGAGGAAA 1
AATGGCCAGAC 2
CGAGGAGTTTT 3
TGTTTTTGTGC 3
GGAAAATGACG 2
TTCCTGATGGT 3
CTAGAAGCTCA 3
GGGTCCAGACT 1
GGAACTCCAGC 1
AACAACTCAGT 2
CCGATACCTGC 1
GCATAAAATTG 1
AACGGGTTCGC 2
TCCTTTGTCTG 2
TTTGGAAAAAG 2
TAGTGGCATCG 1
CTAAAGTGGAA 1
CTCGGGTAGAG 1
GATTTATGAAC 3
AGTTCCACTAA 3
ATTGAGTAATG 3
aattaaacttt 1
TCCGCAGTCAG 2
CGAGAACTCGG 3
GAAGGCAATAG 1
ATGTCAATGAT 2
TCAAAGTGCCT 1
aagagcgctcc 1
TTCGAACCGCC 3
TCAATGGGTGC 3
CGACCTCATTG 1
agaatcagaTC 2
CAGTGGAACCA 1
AGGAAATCCCG 1
AATCAAAAGAA 1
CCGAATCTTCT 2
GATCTTCAGGA 1
ACTCTACTAAA 2
CTATTGTAGCA 2
ATTAAATAGCT 1
AGCGAAGCGCA 1
CGATCTGGCCA 2
TTCGCCAGAGA 2
GTAGTCAGTAA 1
GCAAAGAAAAA 2
GGTGCCACCAG 1
GCTGGACGAGG 3
GGAACCCGAAA 2
TTAATCACTGT 1
GATCGATTCTT 1
AAAGAC

While it is useful to know the distribution of k-mers for a set of sequences, there are some applications like sequence alignment that you also need to know the position. Since we have seen that some k-mers occur more than once, we need to be able to hold multiple positions for each k-mer. What changes to the above code do we need to make to hold the locations of each k-mer?

In [ ]:
reader = FASTAReader(open('subset.fa'))
kmers = {}

k = 11

for seq_id, sequence in reader:
    for i in range(0, len(sequence) - k):
        kmer = sequence[i:i + k]
        kmers.setdefault(kmer, [])
        kmers[kmer].append(i)

for key in kmers:
    print(key, kmers[key])

GTACAAGAATG [425]
AACACCCTTCT [1673]
AGTATATAAGA [658]
CCACCTGTAGA [212]
CGTCTCCGCAA [531, 531]
CACCATGGCTC [217, 217, 217]
TTCGCTTATAA [599]
CGATTGAAACA [10394, 10448]
TGGGACATAGC [584, 464]
AACTGCAACCA [16191, 16245]
TATTCATTTTT [4081]
TTTGGCAGCGG [394]
AATAGTTCAAA [252]
CTTTGGAAGGG [2364, 2364]
CAGAGCCCACA [1648]
TGAGTTCGAGG [7800, 7854]
CTGTGTGCGGT [412]
GTATAAACACA [4320]
TGGACGTGGTG [1008]
GATGTGGACAG [357, 256]
ATTTTGCTGAC [896, 896]
GCTCAGCTGCT [888]
TGGTCATAAGC [775]
AATAGCTATTG [28]
CTGAGCTTTAT [507]
GGACTACGCCT [213, 213]
ACAGTCTGGAA [581]
GCTGAGGGCAT [1231]
GCCCTTGCATT [2582]
ATGATTCCCGA [2796, 3584]
TTGAGCTACTG [3352, 3352]
GGGCGCATCAC [1250, 1250]
TCAGAATGCCA [11106, 11160]
AAAACTTAAGC [2665]
GCTCGTTCCAC [275, 174]
CATACCACTGT [14923, 14977]
CCTGGATGCGA [284]
AGGATAAGCAG [686]
TTTTCCTAATA [40]
GCTATTATCAT [1, 1]
GCCAGAAGAAA [1195, 2397]
GGTCATCAGGG [1945, 1945]
TGCAGCCAGGA [16274, 16328]
ATTGATCTTTC [4171]
GTTAAGTCTGG [1131, 1131, 1919]
CGTGTGTATAT [2603, 2603]
TAAGTATTCA

TTTaaaaagaa [17501]
TGGTCGATCAC [2322, 2322]
CCACACACAGC [1426]
TGATTACCAGT [279]
TGCCGGACTTA [1]
GGCTTCTTCTT [273]
ACAACATGGTC [3189]
GAACCAAGATG [178, 178, 398]
CATCGCCATTG [2649, 12367, 12952]
CCGGGAACCAA [2086]
TCGGCGGGAGG [5893, 15611, 16196]
AATTTTTGCAT [4857, 964]
GGATTAAATCG [2541]
CCACCGTCCTG [2316]
TAACCGCAAGA [79, 79]
TGAACTTGTCC [56]
CTTTCATTTCC [4455]
TTCGACAAGGA [1289]
GATATTGTGGT [1748, 1748]
ATAAATACATT [2129, 2349, 1736]
GTTATATTTAC [1463, 1463, 1683]
CCGCTTACCAA [1345]
TAGGTTTTTAA [1182, 1182]
TACTGGGGCCG [619, 619]
TATTCaaaaaa [5896, 435, 435, 1223]
TGCTACGAAAT [2606, 2423]
GTGCTGCACCA [14905, 14959]
GCCGGACTGGG [869, 869]
GGTGGCTGCTT [3679]
GATTTGTACAA [1649]
TCTACATCTGG [447, 327]
TCCTGATTTGA [8145, 8199]
GACTCCTATCG [2200]
AAAAAAGAATC [2593, 2410]
GCTGGGCAAAA [945]
TGAATGGGACT [1387]
GGGATCACTGC [1579]
CTTTCAATACT [176]
GTACGAGCGCA [658, 658]
TGCGTGGTCCA [134]
TGCTCACCTAC [1001]
GATGCCAAGCA [906]
CCAAAGAGCGC [2335, 2335]
AGACTCAACCC [2556]
CCTACCGAAAT [3017]
AATTT

CCAGAAGGTGC [425]
GGTAGGAGCCG [1215, 1215]
AAAGTAGGCTG [11357, 11411]
CAGGGCCTTGA [445]
TAATATAAAAT [4071]
ACCTTTTCATC [810]
CACGGCACGGT [4, 1026]
GATGAAATAAA [2087]
ATCTGGTGGGA [2227]
AAATTGGACGA [3094, 12812, 13397]
gtgtgtgagtg [396, 396]
AGTGCTCGCCG [1244, 257]
ACTATGCAACA [4000, 4054]
GACGCGTACGA [795, 715]
GGGGACCTGCC [660, 660]
CGCTATGCTTT [2206, 2206]
GGGTGAGAAAG [4183, 4183]
CCTGTCttttt [3019, 2792, 2792]
ACCCTATTAAA [3351, 3168]
TAAAAATTCCA [2109, 2329]
GACATGTTGGG [463, 463]
CTACTAAAGGG [781, 1803]
GGAGTACACCC [818]
CCACTTTAGCA [87]
TAGAGCTCACC [558]
AAGTGCCAGGA [2034, 1973, 1762]
TGCCCTAGCTA [473]
CTACACCCTTG [348]
CGCCTTTGGCT [746]
GTACACCGCCA [105]
GTCCTGGGACC [298]
GCCAGGCACCA [190]
AACAGAGATTT [5327]
TTACTCGTAAT [8076, 17794, 18379, 2391]
CCTTACGTGGA [426, 426]
AGAAGATAATG [176, 75]
TACTGGAAGCC [1263]
CTCACGCCAAA [3798]
CGCAAAGTAGC [11468, 11522]
CCGTTTGCGAC [124, 124, 124]
GCAGCTCAATT [5590, 15308, 15893]
GGGTGAACCGA [756, 756]
ATAGATTTAAG [3885]
GGTAGGCCTGC [1915, 1915

CGCCAGCACAT [752]
tttgaattttc [2348, 2287]
AGTGGTGCCTT [16150, 16204]
AGAAATCAAAT [3427]
TCTTCTTCATT [918]
TCAAAGCTGCG [2943, 2943]
GCGGGGTAGGA [2893, 2893, 1803]
TGTGCCCTGCA [1201]
CCAACAGACGG [714]
GCAAAGCAATT [1727]
CGATGCCAGAT [1863]
GGGGCATGTTC [504, 504]
ATTTAAGGCCG [4250]
ATCTTCTCAAC [3802, 3802]
taATCCATCAT [10123]
AGGGGGAGCCC [176]
ATCTACTTAAG [2859, 2676]
AAACTGTCAAA [1706]
TCTAACTGAAC [4934, 4748]
GAGGACTGGTT [391]
ATCATCCCAAG [2369, 2369]
GGGCTATTTTG [1072, 1043, 1039]
CACACTTAGAT [1501]
TGACCGGTCGT [108]
CTAGCACAGTT [5108, 14826, 15411]
TTGTAATTGCT [2704]
CGGTGGACTCG [2303]
ACCTGGTACCA [1115]
GGCGGCATCTA [153]
TTGATATGTAC [3012, 2829]
gatacaaaaaa [2756, 2695]
GAGAGGCGGAT [3024]
CCTCCAGGACA [3923, 3923]
TTCCATGATAG [1899, 1838, 1627]
ATCGTCGTTTT [1241]
TCACCTTCTTT [8797, 8851]
GTATTTTCTTA [2230]
TTTAACTGCGG [1259]
CCAATTGCCAC [1034, 807, 807]
TGGACCTACGT [642, 642]
ACAACTGCATA [6666, 6666]
GCGTGACCTTC [439]
TATAATTTAAT [7263, 16981, 17566]
TCGTGTTGGCT [5428]
GTGGATGCGAA [33

GAGTCAGCTGC [1005]
CTTGTACGTTT [561]
GTGGTCGAAAT [445]
TTTGCTTATAC [1196, 1196]
TTCTACACCAG [14259, 14313]
TCGCCTTCGCG [1463, 1463]
AAAGGATTTCC [1162]
AATGATCTGAT [272, 152]
GCACAAAATAT [536, 536]
AAATATTTAGT [5514]
TCCTATTTCCG [4832, 14550, 15135]
GCCCCCACTAA [251, 251]
ACGCTTAATCT [6721, 16439, 17024]
AGGACCCTGCT [144]
GGTGCTACTCA [1830]
CTGCTGCGGGA [7400, 7454, 6236, 15954, 16539]
CTTTAAGCAAC [5820, 15538, 16123, 1056]
AATGGGCGCAT [270]
ACGGACTACAG [15644, 15698]
TTTACATGTTC [734, 673, 462]
ATTCAGCTGAG [7940, 17658, 18243]
GAGCTGGTGTG [14186, 14240]
TACTTCGGGAG [782]
GTTGTGCTCTC [202]
GTCAAGAATAG [3725]
ACACAAGCCAG [3589]
ATCGCTGGTCG [573, 573]
GCATTGTTAAG [3316]
acatcaggtcc [12123, 12177]
CATCCATATTT [260, 975]
CGTGCTTGCTA [3449, 3449]
TCTTCAATaaa [169, 169]
CAACATCCACA [1034]
TTTAATCGTAC [2189, 2189, 2162, 2118, 2238]
GTAATCTTGCA [4526, 14244, 14829]
CGACAAGGAAT [945, 10663, 11248]
GCACTACCCCC [726, 1928]
GAAAAATCAGA [363]
CCTCAGCAAGC [11155, 11209]
ACATTTTCGAC [1772, 1772]
CGTTTT

...

TAACAGGTGGG [7805, 17523, 18108]
CGGCCAATGCC [1208, 1208]
CTGGCGCCTTT [7000, 7000]
CCTTCGAAGCG [421]
TAATAGCATAA [6430]
CAGGATCAAAA [138]
CGACTACTATG [627]
AAGTTGGAAAT [270, 270]
ACCCATCAGCC [3135]
GCAGCAGTTCG [389, 389]
TCGATGACAGT [266, 20, 20]
CTTTTGAAGGA [759]
GAATTAAAAGC [199]
TCCCCACCAAA [3012]
ACATGTACCAG [2146]
AGTGGACCTCC [15994, 16048]
TACAATTAAAA [2715]
TTAGTTATGCC [3486]
GTTCCTGCAAG [321]
GCCCGGACACA [1147, 1027]
ACCAGACGGGC [230]
acgggagaaga [6279, 6333]
TACCACTTGTG [2117]
GCGAAGGAATA [4972, 4972]
TATCAACATTG [46]
CCTGGCCCTGG [793]
ATGTGaaaaaa [1951, 3153]
CGATGATGCAG [1017]
AAGGGCAAAAT [1299]
GAAGGAGCCCA [6919, 6919]
TCCGGCCAGGT [10016, 10601]
GGAAACAGCCG [1088, 1088]
TCACGGTCTAC [353]
aagcaacatca [8121, 17839, 18424]
GTGTGTGTATA [1203, 1123]
CAAGGACGAAC [287, 1489, 134, 134, 134]
TCGCCTTCCAC [180, 180]
CTTACAACTGG [16158, 16212]
TTAGAGGCACA [4164]
TCTCTAGTTCC [3893, 3947]
CCGCTAGATGG [24]
TCGGTCACAGT [270]
TTGGAGAAGCC [2077, 11795, 12380]
GAGCTCCCGCA [300, 300]
GACCTACAC

CCGTTCGCCCT [493, 493, 1691]
TTACATGTCCA [1654, 1654]
acagctgccgc [859, 859]
CTCAAACAGAA [922]
TGTGTGAAACT [1482]
ACGTATTAAGT [650]
GCAACATTCCC [1084, 857, 857]
AAAATTCTACA [1305]
CCCATCTCTGC [3240, 12958, 13543]
AGTCCACAAAA [1692, 1692]
GGACGATCTGG [6486, 16204, 16789]
ATCGATTAATA [478]
GGCACTGTCCC [568]
TAGGTACAAAT [1573]
TGACGCTAGTC [2753]
AAGCTATCCTT [1663, 1538, 1538, 1511, 1467, 1587]
GCACAGCTGTT [1943, 1943]
TTATGCGAATC [1537, 1537]
GGATCCCAGCC [316]
TGTGTGTATGT [459, 459, 1247]
AAGCGACGGGA [6667, 16385, 16970]
TGCTCAGCTCG [3265]
CGACGTGAAAG [32, 32]
TGCAAATCGTG [2530]
CAGAGACGGCG [989, 989]
GACGACAGCAG [864, 864, 2208, 2996]
AGCAGAAAATG [595]
CGTTATCGACT [2283, 2283]
CCAGAAGCAGT [4337, 4391]
GCGAATGCTGT [262]
ATTTGTTGCTT [7]
CTGGGTAACTA [365]
TCAATCGGCCC [3664, 3664]
TACTGCATTTC [2784, 2784, 1694]
ACCGGCGCTCT [223]
CGGATGTGAAT [1535]
TGACGAGATTC [238]
CGAGTTCTTTT [854, 627, 627]
AGGATCCGGAC [5142, 14860, 15445]
CCGCCGCCAAT [1903, 1903, 813]
ATCCGATTACG [130]
CTACCTTAACA [3077]


TTAAGCTACAA [1114, 1114, 2312]
CGGTCAACCCG [571]
CAGGAGGCAGG [2131]
gcTCCTCAATG [1929, 1929]
CGGTGCTCTCG [290, 290]
TTGGATAAAAT [734]
TTCCACCTGCC [452]
GCACTTTGACC [714]
TCAAGTTTGTT [850]
ACAATGGCGGT [1000, 1000]
GATCTGACCGT [352]
GTAAAGAGCTA [1040, 1040]
AGAACTACAAG [940]
ATTTTAAGGAC [140]
ATCAGCAACTC [9757]
ATGAGAATCAA [79]
CCGTAACGAGG [553, 553]
TCAACGCCTGC [425]
GTATAAATTCT [165, 13]
CATTCATAATA [1233, 1233]
TCTTGTGGAGG [818, 818, 1038]
ACTAGAGCAAA [2003, 1942, 1731]
GTTTCTCAAAC [83]
TTCCGAGTCCG [483, 358, 358, 331, 287, 407]
GCAAGTATAAC [541, 461]
TTCCAAGGCCA [1007, 887]
GATAGCCCCAA [1618]
AAGCGTGTTTC [4720]
GCAGTCAGCGA [723]
CAAGGAATCTA [13412, 13466]
TATAGATTGCT [7937, 7937]
CCAGAGCTCTG [5598, 5652]
TCATGCAGCAG [385, 284]
AGTTTAGTCAA [3035, 2808, 2808]
CCTAACTCAGG [13578, 13632]
CTTTTAAATTC [64]
TGAAAAAGGGG [7392, 7392]
GAGGATCTTTT [1105, 1105, 2303]
GTACCGCCCAT [3180, 3968]
CTATCAATGTG [427]
AGTTATCATGG [1209]
AATTATTTATG [4130]
AACTTTTTAAT [1352]
aggcccagcag [1488, 1488]
CGGTA

TCCTAGTTTAC [9690, 9744]
ATCCGCAAGCT [1179, 1179]
TCTCTTTTAAG [3415]
TACATTGCGAG [6198, 6198]
CGACGGACAGC [176]
AGCGATTCCAG [3384]
GAGGGAGTGAT [120]
TGAGTTAGTTA [1440]
GAGATTAGATA [60]
TGGCCAAAGGC [873]
AGCGGCTACGG [4114, 13832, 14417]
TTTCTTGCGCC [476]
TTCAAACCTCA [2484]
TCGCAGCGTCG [199, 199]
CAGCGTGGAGG [775, 775]
GCTTTCTCGCA [5494, 15212, 15797]
GGAAATGCGTG [6465, 6519]
GGCGAAGACGG [520]
ATGTCAAAAAG [250]
AGGCTCAACTA [9293, 9347]
aaaaaaGAAGA [33]
CGGGCGGCAGT [246, 217, 213]
GCCGTGCGGTT [100]
TTTTTCAGTAT [8]
CAGCGATGATG [7872, 7926]
CAGGAGCGCCA [1038]
ATTATACATTT [2849, 2622, 2622, 916]
ATCTAGCCATA [1256, 1256, 2044]
ACCACTTTAGC [86]
AACGGCGAATT [7904, 7958]
TTGCAAACTTT [4763]
CATTCTGTCAG [2507, 2507]
GAGCGCGCGCG [1186]
AGAAAGCCAAT [3856]
ccgtttcgttt [106, 106]
ATTGAGTACTA [1551, 1324, 1324]
GGACCAGACGG [707, 707]
GCAGTCGCGTA [886]
TGCACCGTGCC [730]
CTTATAGGGAT [958, 575, 811]
GCGCTGGCAGT [2575, 2575, 1485]
AATATGGTGGT [1545, 1545]
GCGAGGCGGGC [2808, 2581, 2581]
GGCACTAATGA [342]
TT

AGAACTATACG [839, 778, 567]
CATTCCCCCAA [1275]
ggaatcaccac [1509]
TGCCAACTCAG [5055, 14773, 15358]
GATGGGACCAG [703, 703]
GTTCTGGTGAA [14800, 14854]
GTGATGACGCA [1341]
TCCTTCTCCCC [141]
GATTCCCACGA [1932, 1932, 842]
TGGACACTGTA [450]
AGCTTGTTTTG [12]
aCTCGATGCCC [3899, 13617, 14202]
ACGCCGAGGAA [277, 277]
CGCCAGGAGCA [12563, 12617]
ATGATTCAAAT [8243, 8297]
GATGCTTAAGT [2964, 12682, 13267]
AAAAAACATTG [1682, 1682, 1902]
CGACATGTGAA [3230, 3047]
CCAATATGTAT [4677]
AGATGCGAGAC [977, 916, 705]
CTAAATAAACA [88, 88]
TGTCGAACCCG [641, 1663]
GAAGTTATCAA [1756]
TTTGGATATTT [2557, 2557]
TATACGATTGT [2424, 2363]
AAGTTGTATGA [18779]
GCGCCACCGCC [661, 661]
GAACCCAAAGG [2399]
CGATTCATAAA [269]
GAACACCGAGG [1004]
CTCGAAAGCCT [978]
GAGCGGTAAGT [18]
TTACCTTTTGC [35]
TAATCAAAGAT [6948, 7002]
ACACGCGTTAC [2442, 2442, 1352]
GATGAGCGACC [4201, 4255]
CAGATTTGTGG [2964, 2964]
AGGTCCACATG [206]
AGAAGCAAAGG [704, 603]
acacacaggct [220, 220]
GTTATTAAACC [325]
CGGCTTCTGCA [700, 700]
AACCAAGGAGG [590, 608, 608]
C